In [ ]:
%pylab inline

#### Load constants ####
import scipy.constants as sc
from matplotlib.colors import LogNorm
import sys
from time import time


# OVERWRITE DEFAULT PLOTTING PARAMETERS
params = {
    'font.family' : 'sans-serif',
    'font.sans-serif' : ['DejaVu Sans', 'Arial', 'Verdana', 'Liberation Sans'],
    'mathtext.default' : 'regular',
    'mathtext.rm' : 'sans',
    'font.size' : 18,
    'legend.fontsize' : 14,
    'axes.labelsize' : 18,
    'axes.titlesize' : 16,
    'figure.titlesize' : 16,
    'lines.linewidth' : 3.0,
    'legend.frameon' : False,
    'legend.numpoints': 1,
}

matplotlib.rcParams.update(params)

# Implementation of laser pulses

Different laser pulses are implemented as functors.
That is, instances of these classes can be evaluated like functions after instantation.

## Complex valued electric field of laser pulses in frequency-space domain

### (1) Gaussian laser pulse

In [ ]:
class GaussPulseFourierSpace(object):
    """ 
        Elecric field of a Gaussian laser pulse.
        That is, a field with Gaussian frequency spectrum and Gaussian transverse envelope.
        Individual frequencies are modeled as plane waves.
        Compare eq. (66) in supplemental material of
        K. Steiniger et al, "Distortions in focusing laser pulses due to spatio-temporal couplings–An analytic description".
        
        Implementation is for a pulse at arbitrary distance z from its focus.
        
        Before propagation, the pulse's electric field in the focus is assumed to be:
            E(ν,x) = ϵ(ν-ν0) * exp{ -x^2/w0^2 } * exp{ -( 2π * SD * (ν-ν0) / w_0 )^2 }
                     * exp{( α_2 + I*α_3 )*(x/w_0)}
                     * exp{- I * .5 * GDD_0 * }
        with
            ϵ(ν) = .5 * sqrt{π} * τ_Laser exp{ -π^2 ν^2 * τ_Laser^2}
            α_2 = 4π * SD * (ν-ν0) / w_0
            α_3 = (w_0 / c) * 4π^2[ ν_0 * θ' * (ν-ν0) + .5 * ( 2*θ' + 2πν_0 * θ'' ) * (ν - ν0)^2 ]
        
        Compare with eq. (17) of the above article.
            
        Be aware, derivatives of the frequency dependent propagation angle θ (θ' = AD),
        and distribution center x_0 (x_0' = SD_0), are with respect to
        the angular frequency Ω, not ν.
    """
    
    def __init__(self
                 , wavelength # central wavelength of the laser, unit: m
                 , fourier_limited_pulse_duration # where the field(!) drops to 1/e,
                                                  # e.g. tau_FWHM,I / sqrt(2. * log(2.)),
                                                  # unit: s
                 , fourier_limited_width_in_focus # where the field(!) drops to 1/e,
                                                  # e.g. w_FWHM,I / sqrt(2. * log(2.)),
                                                  # unit: m
                 , angular_dispersion_in_focus # dθ/dΩ, e.g. tan(α_tilt)/Ω0, unit: rad * s
                 , spatial_dispersion_in_focus # dx/dΩ, unit: m*s
                 , group_delay_dispersion_in_focus # (d^2φ/dΩ^2) unit: s^2
                 , third_order_dispersion_in_focus = 0. # (d^3φ/dΩ^3) unit: s^3
                ):
        self.λ_Laser = wavelength
        self.ν0 = sc.c / self.λ_Laser
        self.Ω0 = 2. * sc.pi * self.ν0
        self.τ0 = fourier_limited_pulse_duration
        self.w0 = fourier_limited_width_in_focus
        self.zR = sc.pi * self.w0**2 / self.λ_Laser #Rayleigh length
        self.AD_foc = angular_dispersion_in_focus
        self.SD_foc = spatial_dispersion_in_focus
        self.GDD_foc = group_delay_dispersion_in_focus
        self.TOD_foc = third_order_dispersion_in_focus
    
    
    def __call__(self, ν, x, z, TD = 0.):
        """ Return real and imaginary part of complex electric field in frequency-space domain
            at given frequency ν and position (x,z), where z is
            the laser propagation direction.
            
            Laser field has the form E = E_amp * e^[-I φ]

            
            ν - is an array of frequencies for which the spectral field is calculated
        """
        return array([ self.amplitude(ν_i, x, z)
                       * array([ cos(self.phase_angle(ν_i, x, z, TD))
                                , - sin(self.phase_angle(ν_i, x, z, TD)) ])
                      for ν_i in ν])
    
    
    def amplitude(self, ν, x ,z):
        """ Real spectral amplitude E_amp of the pulse's electric field.
        """
        return ( self.spectrum(ν) * sqrt(self.w0 / self.w(z)) 
                 * exp( - ( ( x - self.x_c(ν,z) ) / self.w(z) )**2 )
               )
    
    
    def phase_angle(self, ν, x ,z, TD):
        """ Spectral phase φ
                    
            Analytic expectation after propagation of plane waves along z with angular dispersion 
            including initial time delay, spatial dispersion and group-delay dispersion.
        """
        return (+ 2. * sc.pi * ν * z / sc.c
                + 2. * sc.pi * (ν - self.ν0) * TD
                + ( x - self.x_c(ν,z) )**2 * .5 * 2.*sc.pi* ν * self.R_inv(z) / sc.c
                - self.α_3(ν,z) * x / self.w0
                - 0.25 * self.α_3(ν,z)**2 * z / self.zR
                - .5 * arctan( z / self.zR )
                + .5 * self.GDD_foc * ( 2. * sc.pi * (ν - self.ν0) )**2
                + self.TOD_foc * ( 2. * sc.pi * (ν - self.ν0) )**3 / 6.
               )
        
    
    def spectrum(self,ν):
        """ Gaussian spectrum yielding a pulse with an FWHM duration of the intensity of
                tau_FWHM,I = sqrt(2.*ln(2.)) * tau0
        """
        norm = sqrt(sc.pi) * self.τ0 
        return norm * exp(- self.τ0**2 * sc.pi**2 * (ν - self.ν0)**2 )
    
    
    def x_c(self, ν, z):
        """ Center of a frequency's spatial distribution
        """
        return ( 2. * sc.pi * self.SD_foc * (ν - self.ν0)
                 - (sc.c / ( 2. * sc.pi * self.ν0 * self.w0 ) ) * self.α_3(ν,z) * z
               )
    
    
    def w(self,z):
        """ Laser width without dispersion
        """
        return self.w0 * sqrt( 1. + (z / self.zR)**2 )
    
    
    def R_inv(self,z):
        """ Inverse of typical laser curvature R(z) of Gaussian pulses, i.e. 1 / R(z)
        """
        return z / ( z**2 + self.zR**2 )
    
    
    def α_3(self,ν,z):
        """ Initial frequency dependent complex phase expanded up to third
            order in (Ω-Ω0).
            Yet, this takes only first order angular dispersion dθ/dΩ=θ' into account
            and neglects all higher order angular dispersion terms, e.g.
            d^2θ/dΩ^2 = θ'', θ''', ...
        """
        return ( 
            self.ν0 * self.AD_foc * (ν - self.ν0)
            + self.AD_foc * (ν - self.ν0)**2
            - 4. * sc.pi**2 * self.ν0 * self.AD_foc**3 * (ν - self.ν0)**3 / 6.
        ) * 4. * sc.pi**2 * self.w0 / sc.c


### (2) Implementation of library-class which holds a lot of quantities required in the evaluation of the analytically propagated and Fourier-transformed laser pulses

In [ ]:
class FourierSpaceFunctionLibrary(object):
    """ Implementation of functions appearing in the Fourier space complex electric field definition
    """
    
    def __init__(self
                 , wavelength # central wavelength of the laser, unit: m
                 , fourier_limited_pulse_duration # where the field(!) drops to 1/e,
                                                  # e.g. tau_FWHM,I / sqrt(2. * log(2.)),
                                                  # unit: s
                 , fourier_limited_width_in_focus # where the field(!) drops to 1/e,
                                                  # e.g. w_FWHM,I / sqrt(2. * log(2.)),
                                                  # unit: m
                 , angular_dispersion_in_focus # dθ/dΩ, e.g. tan(α_tilt)/Ω0, unit: rad * s
                 , spatial_dispersion_in_focus # dx/dΩ, unit: m*s
                 , group_delay_dispersion_in_focus # (d^2φ/dΩ^2) unit: s^2
                ):
        self.λ_Laser = wavelength
        self.ν0 = sc.c / self.λ_Laser
        self.Ω0 = 2. * sc.pi * self.ν0
        self.τ0 = fourier_limited_pulse_duration
        self.w0 = fourier_limited_width_in_focus
        self.zR = sc.pi * self.w0**2 / self.λ_Laser #Rayleigh length
        self.AD_foc = angular_dispersion_in_focus
        self.SD_foc = spatial_dispersion_in_focus
        self.GDD_foc = group_delay_dispersion_in_focus
    
    def w(self, z):
        """ Laser width without dispersion
        """
        return self.w0 * sqrt( 1. + (z / self.zR)**2 )
    
    def R_inv(self, z):
        """ Inverse of laser curvature R(z), i.e. 1 / R(z)
        """
        return z / ( z**2 + self.zR**2 )
    
    def beta_2(self, x, z):
        """
        """
        return ( z - self.Ω0 * self.AD_foc * x ) / sc.c
    
    def beta_3(self, z):
        """ Auxialliary quantity.
            See analytical derivation of PFT
        """
        return ( self.AD_foc * z - self.SD_foc ) / self.w(z)
    
    def beta_4(self, z):
        """ Assuming, there are no second order dispersions present
        """
        return self.AD_foc * z / ( self.w(z) * self.Ω0 )
    
    def beta_5(self, z):
        """
        """
        return self.w(z)**2 * self.R_inv(z) / (2. * sc.c)
    
    def beta_6(self, x):
        """ Be aware, that in contrast to the publication,
            beta_6 from the publication is split into
            beta_6 -> beta_6 + beta_7, here.
        """
        return self.AD_foc * x / sc.c
    
    def beta_7(self, z):
        """ This term is part of beta_6 in the publication,
            since they always appear in a pair anyways.
        """
        return self.Ω0 * self.AD_foc**2 * z / (2. * sc.c)
    
    def beta_8(self, x, z):
        """
        """
        assert(False)
    
    def beta_9(self, x, z):
        """
        """
        assert(False)
    
    def gamma_1(self, x, z):
        """
        """
        return ( 1.
            + 8. * x * self.beta_4(z) / ( self.w(z) * self.τ0**2 )
            + 4. * self.beta_3(z)**2 / self.τ0**2
        ) 
    
    def gamma_2(self, x, z):
        """
        """
        w = self.w(z)
        β_3 = self.beta_3(z)
        β_4 = self.beta_4(z)
        β_5 = self.beta_5(z)
        β_6 = self.beta_6(x)
        β_7 = self.beta_7(z)
        return ( .5 * self.GDD_foc - β_6 - β_7 + 2. * x * β_3 * β_5 / w
               + ( 2. * x * β_4 / w + β_3**2 ) * self.Ω0 * β_5
        ) * 4. / self.τ0**2
    
    def gamma_3(self, x, z):
        """
        """
        return -2. * x * self.beta_3(z) / ( self.w(z) * self.τ0 )
    
    def gamma_4(self, t, x, z):
        """
        """
        w = self.w(z)
        β_5 = self.beta_5(z)
        return ( t
            - self.beta_2(x, z)
            - β_5 * (x / w)**2 
            - 2. * x * self.Ω0 * self.beta_3(z) * β_5 / w
        ) / self.τ0


### (3) Gaussian laser pulse keeping only terms of order $(\Omega-\Omega_0)^2$ and lower

In [ ]:
class ApproximateGaussPulseFourierSpace(object):
    """ Compare eq. (97) in supplemental material of
        K. Steiniger et al, "Distortions in focusing laser pulses due to spatio-temporal couplings–An analytic description".
        
        Basically same as `GaussPulseFourierSpace`,
        but all terms of order (Ω-Ω0)**3 and higher are neglected.
        This is the pulse which is analytically Fourier transformed to
        obtain relations for PFT and pulse duration.
    """
    
    def __init__(self
                 , wavelength
                 , fourier_limited_pulse_duration = 30.e-15 / 1.17741 # tau_FWHM,I / sqrt(2. * log(2.))
                 , fourier_limited_width_in_focus = 3.e-6 / 1.17741 # w_FWHM,I / sqrt(2. * log(2.))
                 , angular_dispersion_in_focus = 0. # tan(α_tilt)/(2.*sc.pi*ν0)
                 , spatial_dispersion_in_focus = 0.
                 , group_delay_dispersion_in_focus = 0.
                ):
        self.funcLib = FourierSpaceFunctionLibrary(
            wavelength
            , fourier_limited_pulse_duration
            , fourier_limited_width_in_focus
            , angular_dispersion_in_focus
            , spatial_dispersion_in_focus
            , group_delay_dispersion_in_focus
        )
        self.λ_Laser = self.funcLib.λ_Laser
        self.ν0 = self.funcLib.ν0
        self.Ω0 = self.funcLib.Ω0
        self.τ0 = self.funcLib.τ0
        self.w0 = self.funcLib.w0
        self.zR = self.funcLib.zR #Rayleigh length
        self.AD_foc = self.funcLib.AD_foc
        self.SD_foc = self.funcLib.SD_foc
        self.GDD_foc = self.funcLib.GDD_foc
    
    
    def __call__(self, ν, x, z, TD = 0.):
        """ Return real and imaginary part of the pulse's complex electric field
                E = E_amp * e^[-I φ]
            at given frequency ν and position (x,z), where z is
            the pulse's propagation direction.
            
            ν - is an array of frequencies for which the spectral field is calculated
            TD - is a time delay in order to move the pulse's center position to a location
                different different from z=0 along its propagation axis at t=0.
        """
        return array([ self.amplitude(ν_i, x, z)
                       * array([ cos(self.phase_angle(ν_i, x, z, TD))
                                , - sin(self.phase_angle(ν_i, x, z, TD)) ])
                      for ν_i in ν])
    
    
    def amplitude(self, ν, x ,z):
        """ Real spectral amplitude, includes additional terms from the approximation
        """
        return ( self.spectrum(ν, x, z) * sqrt(self.funcLib.w0 / self.funcLib.w(z)) 
                 * exp( - ( x / self.funcLib.w(z) )**2 )
                 * exp( - 2. * x * self.funcLib.beta_3(z) * 2. * sc.pi * (ν - self.funcLib.ν0) / self.funcLib.w(z) )
               )
    
    
    def phase_angle(self, ν, x , z, TD):
        """ Spectral phase φ
            
            Analytic expectation after propagation of plane waves along z with angular dispersion 
            including initial time delay, spatial dispersion and group-delay dispersion.
        """
        β_2 = self.funcLib.beta_2(x, z)
        β_3 = self.funcLib.beta_3(z)
        β_4 = self.funcLib.beta_4(z)
        β_5 = self.funcLib.beta_5(z)
        β_6 = self.funcLib.beta_6(x)
        β_7 = self.funcLib.beta_7(z)
        
        γ_2 = self.funcLib.gamma_2(x, z)
        γ_4_t_less = self.funcLib.gamma_4(t=0, x=x, z=z)
        
        return ( self.Ω0 * x**2 * self.funcLib.R_inv(z) / (2. * sc.c)
            + self.Ω0 * z / sc.c
            - .5 * arctan( z / self.zR )
            + 0.25 * γ_2 * ( self.τ0 * 2. * sc.pi * (ν - self.ν0) )**2
            - γ_4_t_less * ( self.τ0 * 2. * sc.pi * (ν - self.ν0) )
            + 2. * sc.pi * (ν - self.ν0) * TD
            + .5 * self.GDD_foc * ( 2. * sc.pi * (ν - self.ν0) )**2
        )
        
    
    def spectrum(self, ν, x, z):
        """ Gaussian spectrum yielding a pulse with an FWHM duration of the intensity of
                tau_FWHM,I = sqrt(2.*ln(2.)) * tau0
            Additional terms of order (Ω-Ω)**2 in the real part of the field's exponent are added
            here, too.
        """
        norm = sqrt(sc.pi) * self.τ0
        
        γ_1 = self.funcLib.gamma_1(x, z)
        if not ( γ_1 > 0 ):
            print("Wotcher! Что ты делаешь? γ_1 > 0 ? γ_1 = %f"%(γ_1))
        
        return norm * exp(- γ_1 * ( self.τ0 * sc.pi * (ν - self.ν0) )**2 )


## Implement real-valued time-space domain electric field

### (1) Derive relations of amplitude and phase of frequency-space domain field to the time-space domain field's real part.

A periodic, real function $f(t)$, with a period of $T = (2n + 1)\Delta t$ is trigonometrically interpolated by

$$
  f(t) \approx p_n(t) = \frac{1}{2n+1} \left[
    \frac{a_0}{2} 
    + \sum\limits_{k=1}^{n} a_k \cos(2\pi\nu_k t)
      + b_k \sin(2\pi\nu_k t)
  \right]\,,
$$
where
$$
  \nu_k = \frac{k}{(2n+1)\Delta t}\,.
$$

The coefficients can be calculated from samples of the real space signal at times $t_\ell = \ell\Delta t$ by
$$
\begin{align}
  a_k &= 2 \sum\limits_{\ell=0}^{2n}f(t_\ell)\cos\left( 2\pi \frac{k}{T} t_\ell \right) \\
  b_k &= 2 \sum\limits_{\ell=0}^{2n}f(t_\ell)\sin\left( 2\pi \frac{k}{T} t_\ell \right)\,.
\end{align}
$$

If the real space behavior of a signal is not known, but instead its complex spectrum given,
$$
  \hat f (\nu) = \hat f_\mathrm{amp} (\nu) \exp^{-\imath \varphi(\nu)}
$$
the coefficients $(a_k, b_k)$ can be derived from the connection of the spectrum to the real space signal due to Fourier transformation on the one hand, and to its connection to the complex coefficients $c_k$ of the Fourier series of the real space signal on the other.

That is, starting with the Fourier series
$$
\begin{align}
  f(t) &= \frac{1}{2n+1}\sum\limits_{k=-\infty}^{+\infty} c_k e^{\imath 2\pi\frac{k}{T}t}
        \approx \frac{1}{2n+1}\sum\limits_{k=-n}^{+n} c_k e^{\imath 2\pi\frac{k}{T}t} \\
  c_k &= \frac{1}{\Delta t}\int\limits_{-T/2}^{T/2} f(t) e^{-\imath 2\pi\frac{k}{T}t} dt
       \approx \sum\limits_{\ell = 0}^{2n} f(t_\ell) e^{-\imath 2\pi\frac{k}{T}t_\ell}\,,
\end{align}
$$
to which the coefficients are connected by
$$
\begin{align}
  a_k &= c_k + c_{-k} \\
  b_k &= i( c_k - c_{-k} )\,.
\end{align}
$$
Given the spectrum $\hat f(\nu)$ of the signal, the coefficients $c_k$ can be deduced from the signal's Fourier transform
$$
  f(t) := \int\limits_{-\infty}^{+\infty} \hat f(\nu) e^{\imath 2\pi \nu t} d\nu
$$
which is connected to the complex coefficient by
$$
\begin{align}
  c_k &= \frac{1}{\Delta t}\int\limits_{-T/2}^{T/2}
    \int\limits_{-\infty}^{+\infty} \hat f(\nu)
    e^{\imath 2\pi( \nu - \frac{k}{T} )t} d\nu dt \\
  &= \frac{1}{\Delta t} \int\limits_{-\infty}^{+\infty} \hat f(\nu) \delta\left(\nu - \frac{k}{T}\right) d\nu \\
  &= \frac{1}{\Delta t} \hat f\left( \nu_k = \frac{k}{T} \right)\,.
\end{align}
$$
Therefore,
$$
\begin{align}
  a_k = \frac{1}{\Delta t}\left( \hat f(\nu_k) + \hat f(\nu_{-k}) \right)
    = 2 \Re\left\lbrace \hat f(\nu_k) \right\rbrace / \Delta t
    = 2 \hat f_\mathrm{amp}(\nu_k) \cos\varphi(\nu_k) / \Delta t \\
  b_k = \imath\frac{1}{\Delta t}\left( \hat f(\nu_k) - \hat f(\nu_{-k}) ) \right)
    = - 2 \Im\left\lbrace \hat f(\nu_k) \right\rbrace / \Delta t
    = 2 \hat f_\mathrm{amp}(\nu_k) \sin\varphi(\nu_k) / \Delta t,
\end{align}
$$
provided that $\hat f(\nu_{-k}) = \hat f^\ast(\nu_k)$ such that the coefficients are real.

<span style="color:orange; font-weight:bolder">
    Note, assuming $\hat f(\nu_{-k}) = \hat f^\ast(\nu_k)$ means to have two pulses,
    one at $\Omega = \Omega_0$ and one at $\Omega = -\Omega_0$,
    which effectively doubles the spectral field strength.
    In order to compensate for that, the coefficients of the time domain field are divided by $2$.
</span>

That is,
$$
\begin{align}
  a_k = \hat f_\mathrm{amp}(\nu_k) \cos\varphi(\nu_k) / \Delta t \\
  b_k = \hat f_\mathrm{amp}(\nu_k) \sin\varphi(\nu_k) / \Delta t,
\end{align}
$$

Given the complex spectrum of the field, it is also easy to infer the intensity envelope of the real space signal.
Writing the $c_k$ as
$$
  c_{k,\mathrm{Re}} + \imath c_{k,\mathrm{Im}} = \frac{\hat f_\mathrm{amp}(\nu_k)}{\Delta t}\left[ \cos\varphi(\nu_k) - \imath \sin\varphi(\nu_k) \right]\,,
$$
the sum performed in the construction of $f(t)$ can be performed for the real and imaginary part seperately, yielding
$$
  f(t) = \Re\left\lbrace f(t)\right\rbrace + \imath \Im\left\lbrace f(t)\right\rbrace = f_\mathrm{Re}(t) + \imath f_\mathrm{Im}(t)\,.
$$
The intensity envelope then simply is
$$
  \lvert f(t) \rvert^2 = f(t) \cdot f^\ast(t) = f_\mathrm{Re}(t)^2 + f_\mathrm{Im}(t)^2\,.
$$

### (2) Real-valued time-space electric field from complex-valued frequency-space field

In [ ]:
class RealSpaceLaserPulse(object):
    """ 
        Elecric field of a laser pulse in time-space domain.
        Computed from the frequency-space domain implementation by numerically Fourier transforming with a DFT.
        See derivation above.
    """

    def __init__(self,FourierSpaceLaserPulse, N_λ = 8., N_T = 14.):
        """ Evaluate the sampling parameters for the real space field.
                FourierSpaceLaserPulse - definition of the laser pulse in Fourier space
                N_λ - number of samples per laser wavelength
                N_T - length of time sampling interval in pulse durations
            The latter two parameters define the length and spacing of the sampling interval in spectral domain
        """
        self.spectralLaser = FourierSpaceLaserPulse
        self.Δt = self.spectralLaser.λ_Laser / ( N_λ * sc.c )
        
        sampling_period = N_T * self.spectralLaser.τ0
        self.n_dft = int( ( int( sampling_period / self.Δt ) - 1 ) / 2 )
        print("Number of longitudinal samples =", self.n_dft)
        
        self.ν = arange(0, self.n_dft + 1) / (2. * self.n_dft + 1.) / self.Δt
        self.t = arange(-self.n_dft, self.n_dft+1, 1) * self.Δt ## theroretical range of times to look at

        print("ν_max / ν_0 =", self.ν[-1]/self.spectralLaser.ν0)
        
    
    def __call__(self, x, z):
        """ Return temporal evolution of electric field in real space
            at position (x,z).
            Returns an array with field values at times [-n_dft, n_dft]
            where ( 2*n_dft + 1 ) * Δt = N_T * τ_Laser.
        """
        # Multiplication of the coefficients with .5  here,
        # because I actually have two pulses in frequency-space domain
        # (at ν=ν_0 and ν=-ν_0)
        # in order to comply with f(-ν) = f*(ν) which I need in order 
        # to obtain a purely real signal in time domain.
        # Question: Is this equivalent to taking the real part of the complex
        # signal I would obtain when transforming the complex frequency
        # space pulse defined only for positive frequencies?
        TD = - z / sc.c # Define time delay in order to locate the pulse's temporal origin at the position z where the field is evaluated.
        a0 = self.spectralLaser(array([0.]), x, z, TD)[0][0] / self.Δt
        c = self.spectralLaser(self.ν[1:], x, z, TD)
        a = c[:, 0] / self.Δt
        b = -c[:, 1] / self.Δt
        
        return array([ ( .5*a0 + sum( a * cos( 2. * sc.pi * self.ν[1:] * t_i )
                                      + b * sin( 2. * sc.pi * self.ν[1:] * t_i )
                                    )
                       ) / (2.*self.n_dft + 1)
                       for t_i in self.t
                     ])


### (3) Real-valued time-space intensity envelope from complex-valued frequency-space field

In [ ]:
class RealSpaceIntensityEnvelope(object):
    """ 
        Envelope representing the intensity contour of a laser pulse in time-space domain.
        Computed from the frequency-space domain implementation by numerically Fourier transforming with a DFT.
        See derivation above.
    """
    
    def __init__(self,FourierSpaceLaserPulse, N_λ = 8., N_T = 14.):
        """ Evaluate the sampling parameters for the real space intensity envelope.
                FourierSpaceLaserPulse - definition of the laser pulse in Fourier space
                N_λ - number of samples per laser wavelength
                N_T - length of time sampling interval in pulse durations
            The latter two parameters define the length and spacing of the sampling interval in spectral domain
        """
        self.spectralLaser = FourierSpaceLaserPulse
        self.Δt = self.spectralLaser.λ_Laser / ( N_λ * sc.c )
        
        sampling_period = N_T * self.spectralLaser.τ0
        self.n_dft = int( ( int( sampling_period / self.Δt ) - 1 ) / 2 )
        print("Number of longitudinal samples =", self.n_dft)
        
        self.ν = arange(-self.n_dft, self.n_dft+1, 1) / (2. * self.n_dft + 1.) / self.Δt
        self.t = arange(-self.n_dft, self.n_dft+1, 1) * self.Δt ## theroretical range of times to look at

        print("ν_max / ν_0 =", self.ν[-1]/self.spectralLaser.ν0)

    
    def __call__(self, x, z):
        """ Return temporal evolution of the laser intensity envelope in time-space domain at position (x,z).
            Returns an array with intensity envelope values at times [-n_dft, n_dft]
            where ( 2*n_dft + 1 ) * Δt = N_T * τ_Laser.
        """
        TD = - z / sc.c # Define time delay in order to locate the pulse's temporal origin at the position z where the field is evaluated.
        c = self.spectralLaser(self.ν, x, z, TD) / self.Δt
        
        c_Real = c[:,0]
        c_Imag = c[:,1]
        
        field_Real = array([ sum( c_Real * cos( 2. * sc.pi * self.ν * t_i )
                                  - c_Imag  * sin( 2. * sc.pi * self.ν * t_i )
                                ) for t_i in self.t ]) / (2.*self.n_dft + 1)
        
        field_Imag = array([ sum( c_Imag * cos( 2. * sc.pi * self.ν * t_i )
                                  + c_Real  * sin( 2. * sc.pi * self.ν * t_i )
                                ) for t_i in self.t ]) / (2.*self.n_dft + 1)
        
        intens_envelope = field_Real**2 + field_Imag**2
        
        return intens_envelope


## Analytic expressions for time-space domain properties of Gaussian laser pulses

### (1) Pulse-front tilt (full term)

In [ ]:
class PulseFrontTiltAnalytically(object):
    """ 
        Calculate the tangent of the pulse-front tilt angle at any position z along the propagation axis.
        Compare eq. (18) in
        K. Steiniger et al, "Distortions in focusing laser pulses due to spatio-temporal couplings–An analytic description".
    """
    
    def __init__(self,FourierSpaceLaserPulse):
        """ Store the FourierSpaceLaserPulse in order to obtain the 
            laser's parameters.
        """
        self.spectralLaser = FourierSpaceLaserPulse
        self.funcLib = FourierSpaceFunctionLibrary(
            self.spectralLaser.λ_Laser
            , self.spectralLaser.τ0
            , self.spectralLaser.w0
            , self.spectralLaser.AD_foc
            , self.spectralLaser.SD_foc
            , self.spectralLaser.GDD_foc
        )
    
    def __call__(self, z):
        Ω0 = 2.*sc.pi*self.spectralLaser.ν0
        init = - Ω0 * self.spectralLaser.AD_foc
        
        w = self.funcLib.w(z)
        R_inv = self.funcLib.R_inv(z)
        β_3 = self.funcLib.beta_3(z)
        β_5 = self.funcLib.beta_5(z)
        β_7 = self.funcLib.beta_7(z)
        propagation_addition_1 = 2. * sc.c * β_5 * β_3 * Ω0 / w
        propagation_addition_2 = 8. * sc.c * β_3 * (
            β_7 - β_3**2 * β_5 * Ω0 - sc.c * self.spectralLaser.GDD_foc
        ) / ( w * ( self.spectralLaser.τ0**2 + 4. * β_3**2 ) )
        
        return init + propagation_addition_1 + propagation_addition_2


### (2) Individual terms in pulse-front tilt expression for comparison later

In [ ]:
class PulseFrontTiltAnalyticallyTerm2(object):
    """ Calculate the tangent of the pulse-front tilt angle at any position z along the propagation axis.
    """
    
    def __init__(self,FourierSpaceLaserPulse):
        """ Store the FourierSpaceLaserPulse in order to obtain the 
            laser's parameters.
        """
        self.spectralLaser = FourierSpaceLaserPulse
        self.funcLib = FourierSpaceFunctionLibrary(
            self.spectralLaser.λ_Laser
            , self.spectralLaser.τ0
            , self.spectralLaser.w0
            , self.spectralLaser.AD_foc
            , self.spectralLaser.SD_foc
            , self.spectralLaser.GDD_foc
        )
    
    def __call__(self, z):
        Ω0 = 2.*sc.pi*self.spectralLaser.ν0

        w = self.funcLib.w(z)
        R_inv = self.funcLib.R_inv(z)
        β_3 = self.funcLib.beta_3(z)
        β_5 = self.funcLib.beta_5(z)
        β_7 = self.funcLib.beta_7(z)
        propagation_addition_1 = 2. * sc.c * β_5 * β_3 * Ω0 / w
        
        return propagation_addition_1


In [ ]:
class PulseFrontTiltAnalyticallyTerm3(object):
    """ Calculate the tangent of the pulse-front tilt angle at any position z along the propagation axis.
    """
    
    def __init__(self,FourierSpaceLaserPulse):
        """ Store the FourierSpaceLaserPulse in order to obtain the 
            laser's parameters.
        """
        self.spectralLaser = FourierSpaceLaserPulse
        self.funcLib = FourierSpaceFunctionLibrary(
            self.spectralLaser.λ_Laser
            , self.spectralLaser.τ0
            , self.spectralLaser.w0
            , self.spectralLaser.AD_foc
            , self.spectralLaser.SD_foc
            , self.spectralLaser.GDD_foc
        )
    
    def __call__(self, z):
        Ω0 = 2.*sc.pi*self.spectralLaser.ν0
        
        w = self.funcLib.w(z)
        R_inv = self.funcLib.R_inv(z)
        β_3 = self.funcLib.beta_3(z)
        β_5 = self.funcLib.beta_5(z)
        β_7 = self.funcLib.beta_7(z)
        
        propagation_addition_2 = 8. * sc.c * β_3 * (
            β_7 - β_3**2 * β_5 * Ω0 - sc.c * self.spectralLaser.GDD_foc
        ) / ( w * ( self.spectralLaser.τ0**2 + 4. * β_3**2 ) )
        
        return propagation_addition_2


### (3) Pulse front

In [ ]:
class PulseFront(object):
    """ Calculate the time offset t_0 of the real space field, which depends on the transverse coordinate x,
        at any position z along the propagation axis.
    """
    
    def __init__(self,FourierSpaceLaserPulse):
        """ Store the FourierSpaceLaserPulse in order to obtain the 
            laser's parameters.
        """
        self.spectralLaser = FourierSpaceLaserPulse
        self.funcLib = FourierSpaceFunctionLibrary(
            self.spectralLaser.λ_Laser
            , self.spectralLaser.τ0
            , self.spectralLaser.w0
            , self.spectralLaser.AD_foc
            , self.spectralLaser.SD_foc
            , self.spectralLaser.GDD_foc
        )
    
    def __call__(self, x, z):
        #init = - self.Ω0 * self.spectralLaser.AD_foc
        
        Ω0 = self.spectralLaser.Ω0
        τ0 = self.spectralLaser.τ0
        w = self.funcLib.w(z)
        R_inv = self.funcLib.R_inv(z)
        zR = self.spectralLaser.zR
        β_2 = self.funcLib.beta_2(x, z = 0) # Neglect the z dependence in order to draw te pulse-front always through the center of the pulse.
        β_3 = self.funcLib.beta_3(z)
        β_4 = self.funcLib.beta_4(z)
        β_5 = self.funcLib.beta_5(z)
        β_6 = self.funcLib.beta_6(x)
        β_7 = self.funcLib.beta_7(z)
        
        second = β_5 * x**2 / w**2
        
        third = 2. * (x / w) * β_3 * Ω0 * β_5
        
        GDD = (
            self.spectralLaser.GDD_foc
            + 4. * β_3 * β_5 * x / w 
            + 2. * ( 2. * β_4 * x / w + β_3**2 ) * Ω0 * β_5
            - 2. * (β_6 + β_7)
        )
        
        tau2 = τ0**2 + 8. * β_4 * x / w + 4. * β_3**2
        
        fourth = - 4. * ( x * β_3 / w) * GDD / tau2
        
        t0 = β_2 + second + third + fourth
        
        γ_1 = self.funcLib.gamma_1(x, z)
        if not ( γ_1 > 0 ):
            print("Wotcher! Что ты делаешь? γ_1 > 0 ? γ_1 = %f"%(γ_1))
        
        return t0


### (4) Pulse duration

In [ ]:
class PulseDurationAnalytically(object):
    """ Calculate the pulse duration as the FWHM of the real space intensity
        at any position z along the propagation axis.
    """
    
    def __init__(self,FourierSpaceLaserPulse):
        """ Store the FourierSpaceLaserPulse in order to obtain the 
            laser's parameters.
        """
        self.spectralLaser = FourierSpaceLaserPulse
        self.funcLib = FourierSpaceFunctionLibrary(
            self.spectralLaser.λ_Laser
            , self.spectralLaser.τ0
            , self.spectralLaser.w0
            , self.spectralLaser.AD_foc
            , self.spectralLaser.SD_foc
            , self.spectralLaser.GDD_foc
        )
    
    def __call__(self, z):
        """
        """
        τ0 = self.spectralLaser.τ0
        γ_1_center = self.funcLib.gamma_1(x=0, z=z)
        γ_2_center = self.funcLib.gamma_2(x=0, z=z)
        return τ0 * sqrt( γ_1_center + γ_2_center**2 / γ_1_center )
        
        


# Implementation of library-class which computes dispersion parameters in the focus of an off-axis parabola from parameters before focusing at the parabola

Compare with sec. "Deriving pulse dispersion in the focus of an off-axis parabola" in K. Steiniger et al, "Distortions in focusing laser pulses due to spatio-temporal couplings–An analytic description".

In [ ]:
from scipy.misc import derivative as scipy_misc_derivative 


class DispersionInFocus(object):
    """ Calculate disperison properties (SD, AD, GDD, TOD, ...) of a laser pulse in the
        focus of a parabola from its values before the mirror.
        The in-focus values are available by accessing the corresponding member variables directly
    """
    
    def __init__(self
                 , wavelength = 800.e-9 # wavelength of the central laser frequency
                                        # unit: m
                 , parent_focal_distance = 2.5 # distance of the focal point from the vertex of the parabola
                                               # unit: m
                 , deflection_angle = 45. * sc.pi / 180. # deflection angle of the central frequency for
                                                         # incidence parallel to the axis of the parabola
                                                         # unit: rad
                 , angular_dispersion_at_mirror = 0. # dθ/dΩ, unit: rad*s, z.B. tan(α_tilt)/(2.*sc.pi*ν0)
                                                     # = (dθ/dλ)*(dλ/dΩ) = (dθ/dλ) * (-1) * λ0^2 / (2πc)
                 , spatial_dispersion_at_mirror = 0. # dx/dΩ, unit: m*s, 
                                                     # = (dx/dλ)*(dλ/dΩ) = (dx/dλ) * (-1) * λ0^2 / (2πc)
                 , group_delay_dispersion_at_mirror = 0. # (d^2φ/dΩ^2), unit: s^2
                                                         # = (d^2φ/dν^2)*(dν/dΩ)^2 = (d^2φ/dν^2) / (2π)^2
                 , third_order_dispersion_at_mirror = 0. # (d^3φ/dΩ^3), unit: s^3
                                                         # = (d^3φ/dν^3)*(dν/dΩ)^3 = (d^3φ/dν^3) / (2π)^3
                ):
                
        self.λ0 = wavelength
        self.ν0 = sc.c / self.λ0
        self.f = parent_focal_distance
        self.ψ_defl0 = deflection_angle
        self.f_eff0 = parent_focal_distance / cos( .5 * self.ψ_defl0 )**2 # effective focal distance of parabola
                                                                          # for central frequency
        self.ξ_s0 = 2. * self.f * tan( .5 * self.ψ_defl0 ) # point of incidence of central frequency on parabola
        self.AD_mirr = angular_dispersion_at_mirror
        self.SD_mirr = spatial_dispersion_at_mirror
        self.GDD_mirr = group_delay_dispersion_at_mirror
        self.TOD_mirr = third_order_dispersion_at_mirror
        self.h = 1.e-4*self.ν0 # step size for finite difference approximation of derivatives
        self.dνdΩ = 1. / ( 2. * sc.pi ) # inner derivative with respect to Ω of functions
                                        # defined with respect to ν
        self.SD_foc = self.calc_SD_in_focus()
        self.AD_foc = self.calc_AD_in_focus()
        self.GDD_foc = self.calc_GDD_in_focus()
        self.TOD_foc = self.calc_TOD_in_focus()
    
    
    def __call__(self):
        print("Parent focal distance = %.1fmm; Effective focal distance = %.1fmm"%(self.f*1.e3, self.f_eff0*1.e3))
        CONV_MS_TO_MpM = 1. / ( -1*self.λ0**2 / (2.*sc.pi*sc.c) )
        print("SD @ mirror = %.3emm/nm; SD @ focus = %.3emm/nm"%(self.SD_mirr * CONV_MS_TO_MpM * 1.e-6, self.SD_foc * CONV_MS_TO_MpM * 1.e-6))
        CONV_RADS_TO_RADpM = CONV_MS_TO_MpM
        print("AD @ mirror = %.3eµrad/nm; AD @ focus = %.3eµrad/nm"%(
            self.AD_mirr * CONV_RADS_TO_RADpM * 1.e-3
            , self.AD_foc * CONV_RADS_TO_RADpM * 1.e-3
        ))
        print("PFT @ mirror = %.3edeg; PFT @ focus = %.3edeg"%(
            arctan(2.*sc.pi*self.ν0 * self.AD_mirr ) * 180./ sc.pi
            , arctan(2.*sc.pi*self.ν0 * self.AD_foc ) * 180./ sc.pi
        ))
        print("GDD @ mirror = %.3efs^2; GDD @ focus = %.3efs^2"%(self.GDD_mirr*(1.e15)**2, self.GDD_foc*(1.e15)**2))
        print("TOD @ mirror = %.3efs^3; TOD @ focus = %.3efs^3"%(self.TOD_mirr*(1.e15)**3, self.TOD_foc*(1.e15)**3))
        
    def calc_AD_in_focus(self):
        """ Angular dispersion (AD_{foc,coupl}) in focus obtained from first derivative of frequency dependent
            angle enclosed by the propagation direction of frequency ν and the central frequency ν0
            
            Eq. (22)
        """
        return - self.SD_mirr / self.f_eff0 - self.AD_mirr

    def calc_SD_in_focus(self):
        """ Sptial dispersion (SD_{foc,coupl}) in focus obtained from first derivative of
            distance between spatial distribution centers of frequency ν
            and the central frequency ν0
            (Derivative performed analytically. Only result here.)
            
            Eq. (23)
        """
        return self.f_eff0 * self.AD_mirr
    
    def calc_GDD_in_focus(self):
        """ Group delay dispersion (GDD_{foc,coupl}) in the focus obtained from second derivative of the phase
        
            Eq. (24)
        """
        return -2. * sc.pi * self.ν0 * (
            self.f_eff0 * self.AD_mirr**2 + 2. * self.SD_mirr * self.AD_mirr
        ) / sc.c + self.GDD_mirr
    
    def calc_TOD_in_focus(self):
        """ Third order dispersion (TOD_{foc,coupl}) in focus obtained from third derivative of the phase
        
            Eq. (25)
        """
        return 3. * self.AD_mirr * (
            2. * sc.pi * self.ν0 * self.ξ_s0 * self.SD_mirr * self.AD_mirr / self.f
            - self.f_eff0 * self.AD_mirr
            - 2. * self.SD_mirr
        ) / sc.c + self.TOD_mirr
    
    def f_eff(self, ν):
        """ Frequency dependent effective focal distance.
        """
        return self.ξ_s(ν) / sin( self.ψ_defl(ν) )
    
    def ψ_defl(self, ν):
        """ Frequency dependent deflection angle at parabola
        """
        return 2. * arctan2( self.ξ_s(ν), 2.*self.f )
    
    def ξ_s(self, ν):
        """ x coordinate of the point where incident ray of frequency ν
            intersects with the parabola surface
        """
        p = (self.ξ_s0 - self.x_0(ν))
        q = 0.25 * self.ξ_s0**2 / self.f
        return p + (q - 0.25*p**2/self.f) * self.θ_0(ν)
    
    def θ_0(self, ν):
        """ Angle enclosed by the propagation direction of frequency ν
            and the central frequency ν0 before deflection at the parabola
        """
        return self.AD_mirr * 2. * sc.pi * (ν - self.ν0)
    
    def x_0(self, ν):
        """ Distance between the spatial distribution center of frequency ν
            and the central frequency ν0 before deflection at the parabola
        """
        return self.SD_mirr * 2. * sc.pi * ( ν - self.ν0 )


# Plot intensity map and pulse-front for Gauss with tilt and dispersion values calculated from values before focusing mirror, Fig. 6.

## (1) Input (dispersion) values (before off-axis parabola)

In [ ]:
# central wavelength of laser
wavel = 800.e-9

# pulse duration
pulse_dur = 30.e-15 / 1.17741

# deflection angle at parabola
ψ_defl0 = 90. * sc.pi / 180.

# f/# of off-axis parabola
f_num = 2.5

# beam size at parabola
D = 100.e-3

# Conversion factor from derivative with respect to wavelength λ
# to derivative with respect to frequency Ω
dλdΩ = (-1.) * wavel**2 / (2.*sc.pi*sc.c)

# angular dispersion at parabola
# as Δθ/ΔΩ from Δθ/Δλ in µrad/nm
AD_in = -1. * 1.e-6 / 1.e-9 * dλdΩ

# spatial dispersion at parabola
# as Δx/ΔΩ from Δx/Δλ in mm/nm
SD_in = -0. * 1.e-3 / 1.e-9 * dλdΩ

# group delay dispersion at parabola
# as Δ^2φ/ΔΩ^2 from Δ^2φ/ΔΩ^2 in (fs)^2
GDD_in = 0. * (1.e-15)**2

# third order dispersion at parabola
# as Δ^3φ/ΔΩ^3 from Δ^3φ/ΔΩ^3 in (fs)^3
TOD_in = 0. * (1.e-15)**3

## (2) Compute disperson in focus

In [ ]:
LaserDispersionInFocus = DispersionInFocus(
    wavelength = wavel
    , parent_focal_distance = f_num * D *cos( .5 * ψ_defl0 )**2 # assuming f/# is for off-axis parabola,
                                                                # i.e. f/# * D is the effective focal distance
    , deflection_angle = ψ_defl0
    , angular_dispersion_at_mirror = AD_in
    , spatial_dispersion_at_mirror = SD_in
    , group_delay_dispersion_at_mirror = GDD_in
    , third_order_dispersion_at_mirror = TOD_in
)

LaserDispersionInFocus()

## (3) Check whether requirements for neglecting TOD are fulfilled

In [ ]:
print("τ_0 = %e"%(pulse_dur))
FuncLib = FourierSpaceFunctionLibrary(
    wavelength = wavel
    , fourier_limited_pulse_duration = pulse_dur
    , fourier_limited_width_in_focus = focal_width
    , angular_dispersion_in_focus = LaserDispersionInFocus.AD_foc
    , spatial_dispersion_in_focus = 0. #LaserDispersionInFocus.SD_foc
    , group_delay_dispersion_in_focus = 0. #LaserDispersionInFocus.GDD_foc
)
z_check = FuncLib.zR
w_check = FuncLib.w(z_check)
β_3 = FuncLib.beta_3(z_check)
β_4 = FuncLib.beta_4(z_check)
β_5 = FuncLib.beta_5(z_check)
δ_1 = -z_check*LaserDispersionInFocus.AD_foc**3/(6.*w_check)
δ_2 = z_check*LaserDispersionInFocus.AD_foc**2/sc.c
TOD_check = 6.*β_3**2*β_5 + 12.*FuncLib.Ω0*β_3*β_4*β_5 - 6.*δ_2
req1 = 128.*β_3*β_4/pulse_dur**3
print("128 β_3 β_4 / τ_0^3 = %e << 1?"%(req1))
req2 = 11.*TOD_check/pulse_dur**3
print("11 TOD(z) / τ_0^3 = %e << 1?"%(req2))

## (4) Compute time-space domain properties

In [ ]:
focal_width = LaserDispersionInFocus.f_eff0 * wavel / D
print("focal width = %.2fµm"%(focal_width * 1.e6))
""""""
LaserFourierSpace = GaussPulseFourierSpace(
    wavelength = wavel
    , fourier_limited_pulse_duration = pulse_dur
    , fourier_limited_width_in_focus = focal_width
    , angular_dispersion_in_focus = LaserDispersionInFocus.AD_foc
    , spatial_dispersion_in_focus = LaserDispersionInFocus.SD_foc
    , group_delay_dispersion_in_focus = 0. #LaserDispersionInFocus.GDD_foc
)

LaserRealSpace = RealSpaceLaserPulse(LaserFourierSpace, N_λ = 6, N_T = 14)
LaserIntens = RealSpaceIntensityEnvelope(LaserFourierSpace, N_λ = 6, N_T = 14)
LaserTanψ_tilt = PulseFrontTiltAnalytically(LaserFourierSpace)
LaserPulseFront = PulseFront(LaserFourierSpace)

In [ ]:
print("SD_foc * ( Ω_egde - Ω_0 ) / w_0  @ focus = %.2f"%( LaserTanψ_tilt.funcLib.beta_3(0.) / pulse_dur ))
print("T / τ_0 @ focus = %.2f"%( sqrt( LaserTanψ_tilt.funcLib.gamma_1(0., 0.) ) ))
print("Expected ratio of intensity amplitude to undisturbed pulse = %.2f"%( ( LaserTanψ_tilt.funcLib.gamma_1(0., 0.)**2 + LaserTanψ_tilt.funcLib.gamma_2(0., 0.)**2 )**(-0.5) ))

## (5) Set space domain interval of plotting region

In [ ]:
x = sc.c * LaserFourierSpace.τ0 * linspace(-2., 2., 129, endpoint=True) #LaserFourierSpace.w0 * linspace(-5., 5., 129, endpoint=True)
z = LaserFourierSpace.zR * linspace(-5., 1., 7, endpoint=True)

t_norm = LaserFourierSpace.τ0
x_norm = sc.c * LaserFourierSpace.τ0

print("z_R = %.2fµm"%(LaserFourierSpace.zR*1.e6))
print("z ϵ [%.2f, %.2f]z_R"%(z[0]/LaserFourierSpace.zR, z[-1]/LaserFourierSpace.zR))

## (6) Plot intensity map with pulse-front tilt calculation and pulse-front outline

In [ ]:
import functools
from scipy.optimize import curve_fit

def gauss(t, sig, amp, mean):
    return amp * exp(-.5*(t - mean)**2/sig**2)

In [ ]:
i=0
for z_i in z:
    
    intens2D_t = array([ LaserIntens(x_i, z_i) for x_i in x ])
    
    ############################################################
    ## Calculate PFT
    ############################################################
    ## By deducing arrival time of intensity maximum for two different x positions,
    ## where the x positions are equally spaced to the left and right from the pulse's center,
    ## and compute tangent of PFT angle w/ central finite difference.
    ## Note, this is an updated algorithm compared to the one used in the manuscript,
    ## where the finite difference used values in the center (x_center) and off-center (x_out).
    Δx = int(1.*LaserFourierSpace.w0 / abs(x[1]-x[0]))
    x_center = int(.5*len(x-1))
    x_left = x_center - Δx
    x_right = x_center + Δx
    max_center = argmax(intens2D_t[x_center])
    max_left = argmax(intens2D_t[x_left])
    max_right = argmax(intens2D_t[x_right])
    
    tanψ_tilt_num = (
        (sc.c*LaserIntens.t[max_left] - sc.c*LaserIntens.t[max_right])
        / (x[x_left] - x[x_right])
    )
    ψ_tilt_num = arctan(tanψ_tilt_num)
    
    print("pulse-front tilt (numerically) = arctan( (%.2f - %.2f  ) / ( %.2f - %.2f  ) ) = %.2f deg"%(
        LaserIntens.t[max_left] / t_norm
        , LaserIntens.t[max_right] / t_norm
        , x[x_left] / x_norm
        , x[x_right] / x_norm
        , ψ_tilt_num * 180. / pi
    ))
    
    ####################
    ## Additional sample to quantify uncertainty on PFT value
    ####################
    Δx_sample = int(.5*Δx)
    x_left_sample = x_center - Δx_sample
    x_right_sample = x_center + Δx_sample
    max_left_sample = argmax(intens2D_t[x_left_sample])
    max_right_sample = argmax(intens2D_t[x_right_sample])
    
    tanψ_tilt_num_sample = (
        (sc.c*LaserIntens.t[max_left_sample] - sc.c*LaserIntens.t[max_right_sample])
        / (x[x_left_sample] - x[x_right_sample])
    )
    ψ_tilt_num_sample = arctan(tanψ_tilt_num_sample)
    print("pulse-front tilt (numerically) sample = %.2f deg"%(ψ_tilt_num_sample * 180. / pi))
    
    ####################
    ## Estimate uncertainty due to finite sampling on computed pulse-front tilt
    ####################
    ## By adding one cell to each of the determined arrival times in the numerical tangent calculation
    ## For the last z position.
    tanψ_tilt_num_error_max = (
        (sc.c*LaserIntens.t[max_left - 1] - sc.c*LaserIntens.t[max_right + 1])
        / (x[x_left] - x[x_right])
    )
    ψ_tilt_num_error_max = arctan(tanψ_tilt_num_error_max)
    print("Maximum pulse-front tilt (numerically) = %.2f deg"%(ψ_tilt_num_error_max * 180. / pi))

    tanψ_tilt_num_error_min = (
        (sc.c*LaserIntens.t[max_left + 1] - sc.c*LaserIntens.t[max_right - 1])
        / (x[x_left] - x[x_right])
    )
    ψ_tilt_num_error_min = arctan(tanψ_tilt_num_error_min)
    print("Minimum pulse-front tilt (numerically) = %.2f deg"%(ψ_tilt_num_error_min * 180. / pi))

    print("Estimated uncertainty on pulse-front tilt angle = %f°"%(.5 * (ψ_tilt_num_error_max - ψ_tilt_num_error_min) * 180. / pi))
    
    ############################################################
    ## Calculate pulse duration
    ############################################################
    intensGauss = functools.partial(gauss, amp = intens2D_t[x_center][max_center], mean=LaserIntens.t[max_center])
    intensGauss_popt, intensGauss_pcov = curve_fit(intensGauss, LaserIntens.t / LaserFourierSpace.τ0, intens2D_t[x_center], p0 = 1.)
    τ_meas_τ_0 = 2. * intensGauss_popt[0] # measured duration of the field from the standard deviation of the intensity distribution, unit: τ_0
    
    ############################################################
    ## Plot
    ############################################################
    figure(figsize=(16,6))
    
    print("pulse-front tilt (ana) = %.2f deg"%( arctan(LaserTanψ_tilt(z_i)) * 180. / sc.pi ))
    
    subplot(1,2,1)
    
    imshow(intens2D_t * sqrt( LaserTanψ_tilt.funcLib.gamma_1(0., 0.)**2 + LaserTanψ_tilt.funcLib.gamma_2(0., 0.)**2  )
           , cmap = mpl.cm.Reds
           , origin='lower'
           , interpolation='none'
           , aspect='equal'
           , extent=(LaserIntens.t[0] / t_norm
                     , LaserIntens.t[-1] / t_norm
                     , x[0] / x_norm
                     , x[-1] / x_norm
                    )
           , vmin = 0., vmax = 1.
           #, norm=matplotlib.colors.LogNorm(vmin=1.e-0)
          )

    #colorbar(ticks = linspace(0., 1., 6, endpoint=True), format='%.1f')
    
    ####################
    ## Plot theoretical pulse-front contour.
    ####################
    ## Since I plot t on the x axis, and x ond the y axis, the slope of the pulse-front is 90°-ψ_tilt.
    ## Here I use tan( 90°-ψ_tilt ) = 1 / tan( ψ_tilt )
    plot(LaserTanψ_tilt(z_i) * x / sc.c / t_norm, x / x_norm, label=r"analytic PFT = %.2f°"%( arctan(LaserTanψ_tilt(z_i)) * 180. / sc.pi ) )
    plot(tanψ_tilt_num * x / sc.c / t_norm, x / x_norm, '--', label="measured PFT = %.1f°"%(ψ_tilt_num * 180. / pi))
    #plot(array([LaserPulseFront(x_i, z_i) for x_i in x ]) / t_norm, x / x_norm, label="analytic front" )
    print("Difference of pulse maximum arrival time in cells at x=x_right between the analytic and numeric PFT angle = %.1f"%(
        (LaserTanψ_tilt(z_i) - tanψ_tilt_num) * x[x_right] / sc.c / LaserIntens.Δt
    ))
    
    text(-3.5, -1.5, r"measured duration = %.1f$\tau_0$"%( τ_meas_τ_0 ), fontsize=14)
    
    xlabel(r"$t$ [$\tau_0$]")
    ylabel(r"$x$ [$c\tau_0$]")
    
    xlim(-4., 4.)
    #ylim( -.5, .5 )
    
    title("Intensity @ z = %.2f z_R"%(z_i /  LaserFourierSpace.zR))
    
    grid()
    
    legend()
        
    show()
    #savefig("pics/DRACO_intens_ADmir-%.1fmurad-nm_%03i-%.1f-zR.png"%(AD_in / dλdΩ * 1.e6 / 1.e9 ,i, z_i /  LaserFourierSpace.zR), dpi=100, transparent=False, bbox_inches='tight')

    close()
    i+=1

del i

# Plot scaling of pulse-front tilt and pulse duration for a range of AD values and possibly SD at mirror, Figs. 4 and 5

## (1) Input (dispersion) values (before off-axis parabola)

In [ ]:
# central wavelength of laser
wavel = 800.e-9

# pulse duration
pulse_dur = 30.e-15 / 1.17741

# deflection angle at parabola
ψ_defl0 = 90. * sc.pi / 180. # 45. * sc.pi / 180.

# f/# of off-axis parabola
f_num = 2.5 # Fig. 4
f_num = 20. # Fig. 5

# beam size at parabola
D = 100.e-3

# effective focal distance
f_effective = f_num * D
print("effective focal distance of off-axis parabola = %.1fmm"%(f_effective*1.e3))

focal_width = f_effective * wavel / D
print("focal width FWHM = %.2fµm"%(focal_width * 1.17741 * 1.e6))

Rayleigh_length = sc.pi*focal_width**2 / wavel
print("Rayleigh length z_R = %.1fµm"%( Rayleigh_length * 1.e6 ))

# Conversion factor from derivative with respect to wavelength λ
# to derivative with respect to frequency Ω
dλdΩ = (-1.) * wavel**2 / (2.*sc.pi*sc.c)

# angular dispersion at mirror
# as Δθ/ΔΩ from Δθ/Δλ in µrad/nm
AD_mir = array([5.e-3, 1.e-2, 2.5e-2, 5.e-2, 1.e-1, 2.5e-1, 5.e-1, 1.], dtype=longdouble) * 1.e-6 / 1.e-9 * dλdΩ

# spatial dispersion at mirror
# as Δx/ΔΩ from Δx/Δλ in mm/nm
SD_mir = -zeros(len(AD_mir))
print("Spatial dispersion at the mirror [µm/nm] = ", SD_mir / dλdΩ * 1.e6 / 1.e9)

# angular and spatial dispersion in focus
AD_foc = zeros(len(AD_mir), dtype=longdouble)
SD_foc = zeros(len(AD_foc))
GDD_foc = zeros(len(AD_foc))
TOD_foc = zeros(len(AD_foc))
for i, AD_mir_i in enumerate(AD_mir):
    Dispersions = DispersionInFocus(
        wavelength = wavel
        , parent_focal_distance = f_effective *cos( .5 * ψ_defl0 )**2 
        , deflection_angle = ψ_defl0
        , angular_dispersion_at_mirror = AD_mir_i
        , spatial_dispersion_at_mirror = SD_mir[i]
        , group_delay_dispersion_at_mirror = 0.
        , third_order_dispersion_at_mirror = 0.
    )
    AD_foc[i] = Dispersions.AD_foc
    SD_foc[i] = Dispersions.SD_foc
    GDD_foc[i] = Dispersions.GDD_foc
    TOD_foc[i] = Dispersions.TOD_foc
print("Angular dispersion in focus from AD and SD at mirror [µrad/nm] = ", AD_foc / dλdΩ * 1.e6 / 1.e9)
print("Pulse-front tilt in the focus [°] =",  arctan( -2.*sc.pi * sc.c / wavel * AD_foc ) * 180. / sc.pi )
print("Spatial dispersion in focus from AD and SD at mirror [µm/nm] = ", SD_foc / dλdΩ * 1.e6 / 1.e9)
print("Group delay dispersion in focus from AD and SD at mirror [(fs)**2] = ", GDD_foc * (1.e15)**2)
print("Third order dispersion in focus from AD and SD at mirror [(fs)**3] = ", TOD_foc * (1.e15)**3)

print("Pulse elongation in the focus due to GDD [1/τ_0] =", sqrt( 1 + 4. * GDD_foc**2 / pulse_dur**4 ))
print("I NEGLECT GDD_FOC AND TOD_FOC BECAUSE THEY ARE SO LITTLE.")

# group delay dispersion in focus
# as Δ^2φ/ΔΩ^2 from Δ^2φ/ΔΩ^2 in (fs)^2
GDD_foc = 0. * (1.e-15)**2 # well collimated beam: -Ω0 * θ'^2 * z/c

# third order dispersion in focus
# as Δ^3φ/ΔΩ^3 from Δ^3φ/ΔΩ^3 in (fs)^3
TOD_foc = 0. * (1.e-15)**3

In [ ]:
## Calculate value of requirement to neglect third order dispersion in pulse propagation, along central beam axis and at Rayleigh length
z_R = sc.pi * focal_width**2 / wavel
Ω_0 = 2.*sc.pi*sc.c/wavel
SD_z = -AD_foc[4]*z_R
β_3 = -SD_z/focal_width
β_4 = β_3/Ω_0
print("128 β_3 β_4/τ_0^3 = %e"%(128*β_3*β_4/pulse_dur**3))

## (2) Plot progression of the pulse's (dispersion) parameters while propagating through the focus

In [ ]:
## Definitions for the plotting routines
cmap = mpl.cm.gist_rainbow #mpl.cm.winter

norm = mpl.colors.LogNorm(vmin=AD_mir[0] / dλdΩ * 1.e-3, vmax=AD_mir[-1] / dλdΩ * 1.e-3)

cticks = AD_mir / dλdΩ * 1.e-3

clabel = "$AD_{in}$ [µrad/nm]"

colors = [cmap( norm(AD_mir_i / dλdΩ * 1.e-3) ) for AD_mir_i in AD_mir]

z = Rayleigh_length * linspace(-5., 1., 121, endpoint=True)

In [ ]:
## Create list of Fourier space pulses pulses
ListOfFourierSpaceLasers = [
    GaussPulseFourierSpace(
        wavelength = wavel
        , fourier_limited_pulse_duration = pulse_dur
        , fourier_limited_width_in_focus = focal_width
        , angular_dispersion_in_focus = AD_foc[i]
        , spatial_dispersion_in_focus = SD_foc[i]
        , group_delay_dispersion_in_focus = GDD_foc
        , third_order_dispersion_in_focus = TOD_foc
    )
    for i in arange(len(AD_foc))
]

In [ ]:
figure(figsize=(17,6))

ax1 = subplot(1,2,1)
for i, color in enumerate(colors):
    Tanψ_tilt = PulseFrontTiltAnalytically(ListOfFourierSpaceLasers[i])
    plot( z / Rayleigh_length, arctan(Tanψ_tilt(z)) * 180. / sc.pi, color = color )

xlabel(r"$z$ [$z_R$]")
xlim(z[0] / Rayleigh_length, z[-1] / Rayleigh_length)
title("Pulse-front tilt [deg]")
grid()


ax2 = subplot(1,2,2)
for i, color in enumerate(colors):
    Duration = PulseDurationAnalytically(ListOfFourierSpaceLasers[i])
    plot( z / Rayleigh_length, Duration(z) / pulse_dur, color = color )

xlabel(r"$z$ [$z_R$]")
xlim(z[0] / Rayleigh_length, z[-1] / Rayleigh_length)
title("Pulse duration [τ0]")
grid()


cbar = colorbar(
    mpl.cm.ScalarMappable(norm=norm, cmap=cmap)
    , ax = [ax1,ax2]
    , label = clabel
    , ticks = cticks
)

cbar.ax.set_yticklabels([ "%.1e"%(cticks_i) for cticks_i in cticks ])

suptitle(r"$f/%.1f$ OAP, $z_R=%.0f$µm, $SD_{in}=%.0f$µm/nm"%(f_num, Rayleigh_length * 1.e6, SD_mir[0] / dλdΩ * 1.e6 / 1.e9))

show()

close()

## (3) Plot inset showing that PFT != 0 in focus

In [ ]:
figure(figsize=(4,3))

z_zoom = Rayleigh_length * linspace(-0.005, 0.005, 201, endpoint=True)

ax1 = subplot(1,1,1)
for i, color in enumerate(colors):
    Tanψ_tilt = PulseFrontTiltAnalytically(ListOfFourierSpaceLasers[i])
    plot( z_zoom * 1.e6, arctan(Tanψ_tilt(z_zoom)) * 180. / sc.pi, color = color )
    
xlabel(r"$z$ [µm]")
xlim(-0.05, 0.05)
xticks(array([-0.05, 0., 0.05]))
ylim(-.05, .05)
yticks(array([-0.05, 0., 0.05]))
grid()

show()
#savefig("pics/DRACO_PFT-PD-scaling_short-range_w-o-SDin_zoom.png", dpi=100, transparent=False, bbox_inches='tight')

close()

# Form of pulse width function

$$
E \propto e^{-\frac{x^2}{W^2}}\,,\text{ where }
  W^2 = w^2 \frac{\left(1 + 2\frac{x}{w}\frac{2}{\Omega_0\tau_0} \frac{2\theta^\prime z / \tau_0}{w} + \left( \frac{2\theta^\prime z / \tau_0}{w} \right)^2 \right)}
    {\left(1 + 2\frac{x}{w}\frac{2}{\Omega_0\tau_0} \frac{2\theta^\prime z / \tau_0}{w} \right)}\,\text{ for } SD_0 = 0\,.
$$

If $W$ is to keep its meaning of the width of the transverse profile, which it has for a Gaussian Pulse, i.e. in case $(2\theta^\prime z)/(\tau_0 w) \ll 1$, then $x^2/W^2 \rvert_{x=W}=1$.
That is,
$$
\frac{W^2}{w^2} \frac{\left(1 + 2\frac{W}{w}\frac{2}{\Omega_0\tau_0} \frac{2\theta^\prime z / \tau_0}{w} \right)}
  {\left(1 + 2\frac{W}{w}\frac{2}{\Omega_0\tau_0} \frac{2\theta^\prime z / \tau_0}{w} + \left( \frac{2\theta^\prime z / \tau_0}{w} \right)^2 \right)} \stackrel{!}{=} 1
$$
which yields a cubic equation in $W/w$.
$$
\Rightarrow 0 \stackrel{!}{=} 2\frac{W^3}{w^3}\frac{2}{\Omega_0\tau_0} \frac{2\theta^\prime z / \tau_0}{w}
  + \frac{W^2}{w^2}
  - 2\frac{W}{w}\frac{2}{\Omega_0\tau_0} \frac{2\theta^\prime z / \tau_0}{w}
  - \left(1 + \left( \frac{2\theta^\prime z / \tau_0}{w} \right)^2 \right)
$$
$$
\Rightarrow 0 = Ax^3 + Bx^2 + Cx + D\,,\text{ where } C=-A\,, B=1\,, D<0
$$
$$
\Rightarrow 0 = (x^3 - x) A + x^2 + D
$$

In [ ]:
x = linspace(1, 3.5, 100) # = W/w
Ωτ = 10.

rel_walk_off = 10**linspace(-1,1,3)

In [ ]:
print(rel_walk_off)

In [ ]:
figure()
for rel_walk_off_i in rel_walk_off:
    plot(x, (x**3-x)*(rel_walk_off_i*4/Ωτ) + x**2 - 1 - rel_walk_off_i**2, label="%s"%(rel_walk_off_i))
xlabel("W/w")
ylabel(r"Defining equation for W/w")
grid()
legend()
show()
close()

# Test implementations with standard Gauss

## Full spectral field

In [ ]:
FourierGaus = GaussPulseFourierSpace(
    wavelength = 800.e-9 # wavelength of the central laser frequency, unit: m
    , fourier_limited_pulse_duration = 30.e-15 / 1.17741 # tau_FWHM,I / sqrt(2. * log(2.))
    , fourier_limited_width_in_focus = 2.5e-6 / 1.17741 # w_FWHM,I / sqrt(2. * log(2.))
    , angular_dispersion_in_focus = 0. # dθ/dΩ, e.g. tan(α_tilt)/Ω0, unit: rad * s
    , spatial_dispersion_in_focus = 0. # dx/dΩ, unit: m*s
    , group_delay_dispersion_in_focus = -1000. * (1.e-15)**2 # (d^2φ/dΩ^2) unit: s^2
    , third_order_dispersion_in_focus = 0. * (1.e-15)**3 # (d^3φ/dΩ^3) unit: s^3
)
RealGaus = RealSpaceLaserPulse(FourierGaus, N_λ = 8., N_T = 20.) #N_T = 7.)
IntensGaus = RealSpaceIntensityEnvelope(FourierGaus, N_λ = 8., N_T = 20.) #N_T = 7.)

### Check spectrum of gaus in Fourier space

In [ ]:
figure()

plot((RealGaus.ν/FourierGaus.ν0 - 1.), FourierGaus(RealGaus.ν, 0., 0.))
xlabel("$(\Omega-\Omega_0)/\Omega_0$")
ylabel("$\hat E$")

grid()

show()
close()

In [ ]:
figure()

plot((IntensGaus.ν/FourierGaus.ν0 - 1.), FourierGaus(IntensGaus.ν, 0., 0.))

xlabel("$(\Omega-\Omega_0)/\Omega_0$")
ylabel("$\hat E$")

grid()

show()
close()

### Check field calculation by comparing to expected field and envelope at x=z=0

In [ ]:
figure(figsize=(16,12))
plot(RealGaus.t/FourierGaus.τ0, RealGaus(0., 0.,), label="DFT")
plot(RealGaus.t/FourierGaus.τ0, exp(- (RealGaus.t/FourierGaus.τ0)**2 ), label="field envelope")
plot(RealGaus.t/FourierGaus.τ0
     , exp(- (RealGaus.t/FourierGaus.τ0)**2 )*cos(2.*sc.pi*FourierGaus.ν0*RealGaus.t)
     , '.', ms=12,label="Gauss field")
xlabel("t [τ_Laser]")
ylabel("E")

grid()

legend()

show()
close()

### Check intensity calculation by comparing to expected intensity at x=z=0

In [ ]:
figure(figsize=(16,12))
plot(IntensGaus.t/FourierGaus.τ0, IntensGaus(0., 0.,), label="DFT")
#plot(IntensGaus.t/FourierGaus.τ0, exp(- 2.*(IntensGaus.t/FourierGaus.τ0)**2 )
#     , ".", label="intensity envelope")
xlabel("t [τ0]")
ylabel("I")

ylim(0., 0.5)

grid()

legend()

show()
close()

### Calculate field in (t,x) domain

In [ ]:
x = linspace(-2.*FourierGaus.w0, 2.*FourierGaus.w0, 65)
z = FourierGaus.zR * linspace(0., 1., 5, endpoint=True)

print("z ϵ [%.2f, %.2f]z_R"%(z[0]/FourierGaus.zR, z[-1]/FourierGaus.zR))

In [ ]:
for z_i in z:
    
    t_norm = FourierGaus.τ0
    x_norm = FourierGaus.w0
    
    field2D_t = array([ RealGaus(x_i, z_i) for x_i in x ])

    intens = abs(field2D_t)**2

    x_center = len(x)//2
    max_center = argmax(intens[x_center])
    x_out = int(x_center + 1.*FourierGaus.w0 / abs(x[1]-x[0]) )
    max_out = argmax(intens[x_out])
    
    figure(figsize=(16,6))
    
    print("Verkippung = arctan( (%.2f - %.2f  ) / ( %.2f - %.2f  ) ) = %.2f deg"%(
        RealGaus.t[max_center] / t_norm
        , RealGaus.t[max_out] / t_norm
        , x[x_center] / (sc.c*t_norm)
        , x[x_out] / (sc.c*t_norm)
        , arctan((sc.c*RealGaus.t[max_center] - sc.c*RealGaus.t[max_out]) / (x[x_center] - x[x_out]))*180./pi)
    )
    
    subplot(1,2,1)
    
    imshow(intens,cmap = mpl.cm.Reds
           , origin='lower'
           , interpolation='none', aspect='auto'
           , extent=(RealGaus.t[0] / t_norm, RealGaus.t[-1] / t_norm
                     , x[0] / x_norm, x[-1] / x_norm )
           #, norm=matplotlib.colors.LogNorm(vmin=1.e-0)
          )

    colorbar()
    
    xlabel(r"$t$ [$\tau_0$]")
    ylabel(r"$x$ [$w_0$]")
        
    title("z = %.2f z_R"%(z_i /  FourierGaus.zR))
    
    grid()
        
    show()
    
    close()


## Approximated spectral field

Using the field that is actually Fourier transformed for the analytic calculation.
That is, the field with highest order of 2 in (Ω-Ω0)

In [ ]:
ApproxFourierGaus = ApproximateGaussPulseFourierSpace(
    wavelength = 800.e-9 # wavelength of the central laser frequency, unit: m
    , fourier_limited_pulse_duration = 5.e-15 / 1.17741 # tau_FWHM,I / sqrt(2. * log(2.))
    , fourier_limited_width_in_focus = 3.e-6 / 1.17741 # w_FWHM,I / sqrt(2. * log(2.))
    , angular_dispersion_in_focus = 0. # dθ/dΩ, e.g. tan(α_tilt)/Ω0, unit: rad * s
    , spatial_dispersion_in_focus = 0. # dx/dΩ, unit: m*s
    , group_delay_dispersion_in_focus = 0. # (d^2φ/dΩ^2) unit: s^2
)
ApproxRealGaus = RealSpaceLaserPulse(ApproxFourierGaus, N_λ = 8., N_T = 7.)
ApproxIntensGaus = RealSpaceIntensityEnvelope(ApproxFourierGaus, N_λ = 8., N_T = 7.)

### Check spectrum of gaus in Fourier space

In [ ]:
figure()

plot((ApproxRealGaus.ν/ApproxFourierGaus.ν0 - 1.), ApproxFourierGaus(ApproxRealGaus.ν, 0., 0.))
xlabel("$(\Omega-\Omega_0)/\Omega_0$")
ylabel("$\hat E$")

grid()

show()
close()

In [ ]:
figure()

plot((ApproxIntensGaus.ν/ApproxFourierGaus.ν0 - 1.), ApproxFourierGaus(ApproxIntensGaus.ν, 0., 0.))

xticks(arange(-5, 3+1))

xlabel("$(\Omega-\Omega_0)/\Omega_0$")
ylabel("$\hat E$")

grid()

show()
close()

### Check field calculation by comparing to expected field and envelope at x=z=0

In [ ]:
figure(figsize=(16,12))
plot(ApproxRealGaus.t/ApproxFourierGaus.τ0, ApproxRealGaus(0., 0.,), label="DFT")
plot(ApproxRealGaus.t/ApproxFourierGaus.τ0, exp(- (ApproxRealGaus.t/ApproxFourierGaus.τ0)**2 ), label="field envelope")
plot(ApproxRealGaus.t/ApproxFourierGaus.τ0
     , exp(- (ApproxRealGaus.t/ApproxFourierGaus.τ0)**2 )*cos(2.*sc.pi*ApproxFourierGaus.ν0*ApproxRealGaus.t)
     , '.', ms=12,label="Gauss field")
xlabel("t [τ_Laser]")
ylabel("E")

grid()

legend()

show()
close()

### Check intensity calculation by comparing to expected intensity at x=z=0

In [ ]:
figure()
plot(ApproxIntensGaus.t/ApproxFourierGaus.τ0, ApproxIntensGaus(0., 0.,), label="DFT")
plot(ApproxIntensGaus.t/ApproxFourierGaus.τ0, exp(- 2.*(ApproxIntensGaus.t/ApproxFourierGaus.τ0)**2 )
     , ".", label="intensity envelope")
xlabel("t [τ_Laser]")
ylabel("I")

grid()

legend()

show()
close()

### Calculate field in (t,x) domain

In [ ]:
x = linspace(-2.*ApproxFourierGaus.w0, 2.*ApproxFourierGaus.w0, 64)
z = ApproxFourierGaus.zR * linspace(0., 1., 5, endpoint=True)

print("z ϵ [%.2f, %.2f]z_R"%(z[0]/ApproxFourierGaus.zR, z[-1]/ApproxFourierGaus.zR))

In [ ]:
for z_i in z:
    
    t_norm = ApproxFourierGaus.τ0
    x_norm = ApproxFourierGaus.w0
    
    intens2D_t = array([ ApproxIntensGaus(x_i, z_i) for x_i in x ])

    x_center = len(x)//2
    max_center = argmax(intens2D_t[x_center])
    x_out = int(x_center + 1.*ApproxFourierGaus.w0 / abs(x[1]-x[0]) )
    max_out = argmax(intens2D_t[x_out])
    
    figure(figsize=(16,6))
    
    print("Verkippung = arctan( (%.2f - %.2f  ) / ( %.2f - %.2f  ) ) = %.2f deg"%(
        ApproxRealGaus.t[max_center] / t_norm
        , ApproxRealGaus.t[max_out] / t_norm
        , x[x_center] / (sc.c*t_norm)
        , x[x_out] / (sc.c*t_norm)
        , arctan((sc.c*ApproxRealGaus.t[max_center] - sc.c*ApproxRealGaus.t[max_out]) / (x[x_center] - x[x_out]))*180./pi)
    )
    
    subplot(1,2,1)
    
    imshow(intens2D_t,cmap = mpl.cm.Reds
           , origin='lower'
           , interpolation='none', aspect='auto'
           , extent=(ApproxRealGaus.t[0] / t_norm, ApproxRealGaus.t[-1] / t_norm
                     , x[0] / x_norm, x[-1] / x_norm)
           #, norm=matplotlib.colors.LogNorm(vmin=1.e-0)
          )

    colorbar()
    
    xlabel(r"$t$ [$\tau_0$]")
    ylabel(r"$x$ [$w_0$]")
        
    title("z = %.2f z_R"%(z_i /  ApproxFourierGaus.zR))
    
    grid()
        
    show()
    
    close()


# Gaus with tilt

In [ ]:
wavel = 800.e-9
FourierGausWithAD = GaussPulseFourierSpace(
    wavelength = wavel
    , fourier_limited_pulse_duration = 5.e-15 / 1.17741 # tau_FWHM,I / sqrt(2. * log(2.))
    , fourier_limited_width_in_focus = 3.e-6 / 1.17741 # w_FWHM,I / sqrt(2. * log(2.))
    , angular_dispersion_in_focus = -tan(30.*sc.pi/180.)/(2.*sc.pi*sc.c/wavel)
    , spatial_dispersion_in_focus = 0.
    , group_delay_dispersion_in_focus = 0.
)
RealGausWithAD = RealSpaceLaserPulse(FourierGausWithAD, N_λ = 4., N_T = 7.)
IntensGausWithAD = RealSpaceIntensityEnvelope(FourierGausWithAD, N_λ = 4., N_T = 7.)
Tanψ_tilt = PulseFrontTiltAnalytically(FourierGausWithAD)
Front = PulseFront(FourierGausWithAD)

## Calculate field in (t,x) domain

In [ ]:
x = linspace(-2.*FourierGausWithAD.w0, 2.*FourierGausWithAD.w0, 65)
z = FourierGausWithAD.zR * linspace(-5., 0., 11, endpoint=True)

print("z ϵ [%.2f, %.2f]z_R"%(z[0]/FourierGausWithAD.zR, z[-1]/FourierGausWithAD.zR))

In [ ]:
for z_i in z:
    
    t_norm = FourierGausWithAD.τ0
    x_norm = FourierGausWithAD.w0
    
    intens2D_t = array([ IntensGausWithAD(x_i, z_i) for x_i in x ])

    ## Calculate PFT from field distribution calculated with DFT
    x_center = len(x-1)//2
    max_center = argmax(intens2D_t[x_center])
    x_out = int(x_center + 1.*FourierGausWithAD.w0 / abs(x[1]-x[0]) )
    max_out = argmax(intens2D_t[x_out])
    
    tanψ_tilt_num = ( (sc.c*IntensGausWithAD.t[max_center] - sc.c*IntensGausWithAD.t[max_out])
                      / (x[x_center] - x[x_out]) )
    print("PFT (num) = arctan( (%.2f - %.2f  ) / ( %.2f - %.2f  ) ) = %.2f deg"%(
        IntensGausWithAD.t[max_center] / t_norm
        , IntensGausWithAD.t[max_out] / t_norm
        , x[x_center] / x_norm
        , x[x_out] / x_norm
        , arctan(tanψ_tilt_num) * 180. / pi
    )
    )
    
    print("PFT (ana) = %.2f deg"%( arctan(Tanψ_tilt(z_i)) * 180. / sc.pi ))
    
    figure(figsize=(8,6))
    
    subplot(1,1,1)
    
    imshow(intens2D_t,cmap = mpl.cm.Reds
           , origin='lower'
           , interpolation='none', aspect='auto'
           , extent=(IntensGausWithAD.t[0] / t_norm
                     , IntensGausWithAD.t[-1] / t_norm
                     , x[0] / x_norm
                     , x[-1] / x_norm
                    )
           #, norm=matplotlib.colors.LogNorm(vmin=1.e-0)
          )

    colorbar()
    
    ## Plot theoretical pulse-front contour.
    ## Since I plot t on the x axis, and x ond the y axis, the slope of the pulse-front is 90°-ψ_tilt.
    ## Here I use tan( 90°-ψ_tilt ) = 1 / tan( ψ_tilt )
    plot(Tanψ_tilt(z_i) * x / (sc.c * t_norm), x / x_norm, label="analytic PFT" )
    plot(tanψ_tilt_num * x / (sc.c * t_norm), x / x_norm, label="measured PFT" )
    plot(array([Front(x_i, z_i) for x_i in x ]) / t_norm, x / x_norm, label="analytic Front" )
    
    xlabel(r"$t$ [$\tau_0$]")
    ylabel(r"$x$ [$w_0$]")
    
    title("Intensity @ z = %.2f z_R"%(z_i /  FourierGausWithAD.zR))
    
    grid()
    
    legend()
        
    show()
    
    close()


## Aproximate Gauss pulse with AD

In [ ]:
wavel = 800.e-9
ApproxFourierGausWithAD = ApproximateGaussPulseFourierSpace(
    wavelength = wavel
    , fourier_limited_pulse_duration = 5.e-15 / 1.17741 # tau_FWHM,I / sqrt(2. * log(2.))
    , fourier_limited_width_in_focus = 3.e-6 / 1.17741 # w_FWHM,I / sqrt(2. * log(2.))
    , angular_dispersion_in_focus = tan(30.*sc.pi/180.)/(2.*sc.pi*sc.c/wavel)
    , spatial_dispersion_in_focus = 0.
    , group_delay_dispersion_in_focus = 0.
)
ApproxRealGausWithAD = RealSpaceLaserPulse(ApproxFourierGausWithAD, N_λ = 12., N_T = 7.)
ApproxIntensGausWithAD = RealSpaceIntensityEnvelope(ApproxFourierGausWithAD, N_λ = 12., N_T = 7.)
ApproxTanψ_tilt = PulseFrontTiltAnalytically(ApproxFourierGausWithAD)
ApproxFront = PulseFront(ApproxFourierGausWithAD)

In [ ]:
x = sc.c * ApproxRealGausWithAD.t
z = ApproxFourierGausWithAD.zR * linspace(0., 1., 5, endpoint=True)

print("z ϵ [%.2f, %.2f]z_R"%(z[0]/ApproxFourierGausWithAD.zR, z[-1]/ApproxFourierGausWithAD.zR))

In [ ]:
for z_i in z:
    
    t_norm = ApproxFourierGausWithAD.τ0
    x_norm = ApproxFourierGausWithAD.w0
    
    intens2D_t = array([ ApproxIntensGausWithAD(x_i, z_i) for x_i in x ]) #array([ IntensGausWithAD(x_i, z_i) for x_i in x ])

    ## Calculate PFT from field distribution calculated with DFT
    x_center = len(x-1)//2
    max_center = argmax(intens2D_t[x_center])
    x_out = int(x_center + 1.*ApproxFourierGausWithAD.w0 / abs(x[1]-x[0]) )
    max_out = argmax(intens2D_t[x_out])
        
    tanψ_tilt_num = ( (sc.c*ApproxIntensGausWithAD.t[max_center] - sc.c*ApproxIntensGausWithAD.t[max_out])
                      / (x[x_center] - x[x_out]) )
    print("Verkippung (num) = arctan( (%.2f - %.2f  ) / ( %.2f - %.2f  ) ) = %.2f deg"%(
        ApproxIntensGausWithAD.t[max_center] / t_norm
        , ApproxIntensGausWithAD.t[max_out] / t_norm
        , x[x_center] / x_norm
        , x[x_out] / x_norm
        , arctan(tanψ_tilt_num) * 180. / pi
    )
    )
    
    print("Verkippung (ana) = %.2f deg"%( arctan(ApproxTanψ_tilt(z_i)) * 180. / sc.pi ))
    
    figure(figsize=(8,6))

    subplot(1,1,1)
    
    imshow(intens2D_t,cmap = mpl.cm.Reds
           , origin='lower'
           , interpolation='none', aspect='auto'
           , extent=(ApproxIntensGausWithAD.t[0] / t_norm
                     , ApproxIntensGausWithAD.t[-1] / t_norm
                     , x[0] / x_norm
                     , x[-1] / x_norm
                    )
           #, norm=matplotlib.colors.LogNorm(vmin=1.e-0)
          )

    colorbar()
    
    ## Plot theoretical pulse-front contour.
    ## Since I plot t on the x axis, and x ond the y axis, the slope of the pulse-front is 90°-ψ_tilt.
    ## Here I use tan( 90°-ψ_tilt ) = 1 / tan( ψ_tilt )
    plot(ApproxIntensGausWithAD.t / t_norm, ( 1. / ApproxTanψ_tilt(z_i) ) * sc.c * ApproxIntensGausWithAD.t / x_norm, label="analytic PFT" )
    plot(ApproxIntensGausWithAD.t / t_norm, ( 1. / tanψ_tilt_num ) * sc.c * ApproxIntensGausWithAD.t / x_norm, label="measured PFT" )
    plot(array([ApproxFront(x_i, z_i) for x_i in x ]) / t_norm, x / x_norm, label="analytic Front" )
    
    ylim(x[0] / x_norm, x[-1] / x_norm)
    
    xlabel(r"$t$ [$\tau_0$]")
    ylabel(r"$x$ [$w_0$]")
    
    title("Intensity @ z = %.2f z_R"%(z_i /  ApproxFourierGausWithAD.zR))
    
    grid()
    
    legend()
        
    show()
    
    close()
